In [2]:
import pandas as pd
import plotly.express as px
import json

In [3]:
dataset = pd.read_csv("taxi_partial.csv")

In [4]:
dataset

TRIP_ID CALL_TYPE  ORIGIN_CALL  ORIGIN_STAND   TAXI_ID   TIMESTAMP  \
0        T1         B          NaN          15.0  20000542  1408039037   
1        T2         B          NaN          57.0  20000108  1408038611   
2        T3         B          NaN          15.0  20000370  1408038568   
3        T4         B          NaN          53.0  20000492  1408039090   
4        T5         B          NaN          18.0  20000621  1408039177   
..      ...       ...          ...           ...       ...         ...   
315    T323         A      70885.0           NaN  20000430  1419171485   
316    T324         B          NaN          53.0  20000020  1419170802   
317    T325         C          NaN           NaN  20000207  1419172121   
318    T326         A      76232.0           NaN  20000667  1419171980   
319    T327         A      31208.0           NaN  20000255  1419171420   

    DAY_TYPE  MISSING_DATA                                           POLYLINE  
0          A         False  [[-8.585676, 41.148522], [-8.585712000000001, ...  
1          A         False  [[-8.610876000000001, 41.14557], [-8.610858, 4...  
2          A         False  [[-8.585739, 41.148558], [-8.585730000000002, ...  
3          A         False  [[-8.613963, 41.141169], [-8.614125000000001, ...  
4          A         False  [[-8.619902999999999, 41.148036000000005], [-8...  
..       ...           ...                                                ...  
315        A         False  [[-8.570196, 41.159484], [-8.570187, 41.158962...  
316        A         False  [[-8.613873, 41.14123200000001], [-8.613882, 4...  
317        A         False  [[-8.648100000000001, 41.152536], [-8.647461, ...  
318        A         False  [[-8.571699, 41.156073000000006], [-8.57058300...  
319        A         False  [[-8.574561000000001, 41.180184], [-8.572248, ...  

[320 rows x 9 columns]

In [5]:
dataset.columns

Index(['TRIP_ID', 'CALL_TYPE', 'ORIGIN_CALL', 'ORIGIN_STAND', 'TAXI_ID',
       'TIMESTAMP', 'DAY_TYPE', 'MISSING_DATA', 'POLYLINE'],
      dtype='object')

In [6]:
lst = json.loads(dataset["POLYLINE"].iloc[0])
lon, lat = zip(*lst)
polyline = pd.DataFrame()
polyline["lat"] = lat
polyline["lon"] = lon
polyline["id"] = dataset["TRIP_ID"].iloc[0]
polyline

lat       lon  id
0   41.148522 -8.585676  T1
1   41.148639 -8.585712  T1
2   41.148855 -8.585685  T1
3   41.148927 -8.585730  T1
4   41.148963 -8.585982  T1
5   41.148954 -8.586396  T1
6   41.148720 -8.586072  T1
7   41.147847 -8.586324  T1
8   41.147460 -8.586999  T1
9   41.147154 -8.586576  T1
10  41.146623 -8.584884  T1

In [7]:
df = dataset.loc[:, ["POLYLINE", "TRIP_ID"]]
polylines = pd.DataFrame()
lon, lat, id = [], [], []

for i in range(len(df.index)):
    try:
        lst = json.loads(dataset["POLYLINE"].iloc[i])
        longi, latte = zip(*lst)
        lon = lon+ list(longi)
        lat=lat+list(latte)
        id = id+[dataset["TRIP_ID"].iloc[i] for j in range(len(lst))]
    except:
        print("upsie doopsie")
    
polylines["lat"]=lat
polylines["lon"]=lon
polylines["id"]=id

polylines

lat       lon    id
0      41.148522 -8.585676    T1
1      41.148639 -8.585712    T1
2      41.148855 -8.585685    T1
3      41.148927 -8.585730    T1
4      41.148963 -8.585982    T1
...          ...       ...   ...
14433  41.199111 -8.582562  T327
14434  41.198310 -8.586135  T327
14435  41.197824 -8.590464  T327
14436  41.195223 -8.590779  T327
14437  41.192244 -8.592345  T327

[14438 rows x 3 columns]

In [35]:
fig = px.density_mapbox(polylines, lat="lat", lon="lon", radius=3, zoom=3, height=700)

fig.update_layout(mapbox_style="stamen-terrain", mapbox_zoom=12, mapbox_center_lat = 41.14,
    margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

In [11]:
fig = px.line_mapbox(polylines, lat="lat", lon="lon", color="id", zoom=3, height=700)

fig.update_layout(mapbox_style="stamen-terrain", mapbox_zoom=12, mapbox_center_lat = 41.14,
    margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

In [32]:
from sklearn.cluster import DBSCAN
dbscan=DBSCAN(eps=0.0005,min_samples=10)
dbscan.fit(polylines[['lat','lon']])

polylines['DBSCAN_labels']=dbscan.labels_
polylines_filtered = polylines[polylines.DBSCAN_labels>-1]


fig = px.scatter_mapbox(polylines_filtered, lat="lat", lon="lon", zoom=3, color="DBSCAN_labels", height=700)

fig.update_layout(mapbox_style="stamen-terrain", mapbox_zoom=12, mapbox_center_lat = 41.14,
    margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

In [45]:
for i in range (len(polylines.index)):
    if polylines.iloc[i].DBSCAN_labels==-1:
        id = polylines.iloc[i].id
        if (polylines.iloc[i+1].id ==id && polylines.iloc[i+1].DBSCAN_labels>-1):
            polylines.iloc[i+1].id = polylines.iloc[i+1].id + polylines.iloc[i+1].DBSCAN_labels
        print(id)

T1
T2
T2
T2
T2
T3
T3
T3
T3
T3
T3
T3
T3
T3
T3
T3
T3
T6
T6
T6
T6
T6
T6
T6
T6
T6
T6
T6
T6
T6
T7
T7
T7
T7
T7
T7
T8
T8
T8
T8
T8
T8
T8
T8
T8
T8
T8
T8
T8
T8
T8
T8
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T9
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T10
T12
T12
T12
T12
T13
T13
T13
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T14
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T16
T17
T17
T17
T17
T17
T17
T17
T17
T17
T19
T19
T19
T20
T20
T20
T20
T20
T22
T22
T22
T22
T22
T22
T22
T22
T22
T25
T2

T137
T137
T137
T137
T137
T137
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T138
T139
T139
T139
T139
T139
T139
T139
T139
T140
T140
T140
T140
T140
T140
T140
T140
T140
T140
T140
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T141
T142
T142
T142
T142
T142
T142
T143
T143
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T144
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T145
T146
T146
T146
T146
T146
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148
T148


T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T230
T231
T231
T231
T231
T231
T231
T231
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T233
T235
T235
T235
T235
T235
T235
T235
T235
T235
T237
T237
T237
T237
T237
T237
T237
T237
T237
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T238
T239
T239
T239
T239
T239
T239
T239
T239
T239
T239
T240
T240
T240
T240
T240
T240
T240
T240
T240
T240
T240
T240
T242
T242
T242
T242
T242
T242
T242
T243
T243
T243
T243
T243
T243
T243
T243
T243
T243
T243
T243
T243
T243
T243
T244
T244
T244
T244
T244
T244
T244
T245
T245
T245
T245
T245
T245
T245
T245
T245
T245
T245
T245
T246
T246
T246
T246
T246
T246
T246
T246
T246
T246
T246
T246
T246
T246
T246
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T247
T248
T250
T250
T250
T250
T250
T250
T250
T250
T250
T250
T250
T250


In [61]:
polylines[:15]

lat       lon  id  KMeans_labels  DBSCAN_labels
0   41.148522 -8.585676  T1             23              0
1   41.148639 -8.585712  T1             23              0
2   41.148855 -8.585685  T1             23              0
3   41.148927 -8.585730  T1             23              0
4   41.148963 -8.585982  T1             23              0
5   41.148954 -8.586396  T1             23              0
6   41.148720 -8.586072  T1             23              0
7   41.147847 -8.586324  T1             23              0
8   41.147460 -8.586999  T1             23              0
9   41.147154 -8.586576  T1             23              0
10  41.146623 -8.584884  T1             23             -1
11  41.145570 -8.610876  T2            264              1
12  41.145579 -8.610858  T2            264              1
13  41.145768 -8.610903  T2            264              1
14  41.146191 -8.610444  T2            264              1

In [83]:
new_ids=[]
j=0
for i in range (len(dataset.index)):
    id = dataset.iloc[i].TRIP_ID
    #print(id)
    
    while j<len(polylines.index):
        if polylines.iloc[j].DBSCAN_labels==-1:
            #print('noise: '+ polylines.iloc[j].id)
            new_ids=new_ids+[-1]
            j+=1
            continue
        elif polylines.iloc[j].DBSCAN_labels>-1 and polylines.iloc[j-1].DBSCAN_labels==-1 and polylines.iloc[j].id==polylines.iloc[j-1].id:
            new_ids=new_ids + [str(polylines.iloc[j].id) + str(polylines.iloc[j].DBSCAN_labels) + str(j)]
            #print('elif: '+polylines.iloc[j].id)
        else:
            if(j==0):
                new_ids=new_ids+['T1']
            elif(polylines.iloc[j].id != polylines.iloc[j-1].id):
                new_ids=new_ids+[polylines.iloc[j].id]
            else:
                new_ids=new_ids+[new_ids[-1]]
            #print('else: '+polylines.iloc[j].id)
        j+=1

polylines["new_ids"]=new_ids
polylines[:100]
    

lat       lon  id  KMeans_labels  DBSCAN_labels new_ids
0   41.148522 -8.585676  T1             23              0      T1
1   41.148639 -8.585712  T1             23              0      T1
2   41.148855 -8.585685  T1             23              0      T1
3   41.148927 -8.585730  T1             23              0      T1
4   41.148963 -8.585982  T1             23              0      T1
..        ...       ...  ..            ...            ...     ...
95  41.140809 -8.615259  T4             76             10      T4
96  41.140800 -8.615241  T4             76             10      T4
97  41.140818 -8.615052  T4             76             10      T4
98  41.140980 -8.614638  T4             76             10      T4
99  41.148036 -8.619903  T5            296             11      T5

[100 rows x 6 columns]

In [85]:
polylines[:60]

lat       lon  id  KMeans_labels  DBSCAN_labels new_ids
0   41.148522 -8.585676  T1             23              0      T1
1   41.148639 -8.585712  T1             23              0      T1
2   41.148855 -8.585685  T1             23              0      T1
3   41.148927 -8.585730  T1             23              0      T1
4   41.148963 -8.585982  T1             23              0      T1
5   41.148954 -8.586396  T1             23              0      T1
6   41.148720 -8.586072  T1             23              0      T1
7   41.147847 -8.586324  T1             23              0      T1
8   41.147460 -8.586999  T1             23              0      T1
9   41.147154 -8.586576  T1             23              0      T1
10  41.146623 -8.584884  T1             23             -1      -1
11  41.145570 -8.610876  T2            264              1      T2
12  41.145579 -8.610858  T2            264              1      T2
13  41.145768 -8.610903  T2            264              1      T2
14  41.146191 -8.610444  T2            264              1      T2
15  41.146758 -8.609445  T2              0              1      T2
16  41.147118 -8.608896  T2              0              1      T2
17  41.147127 -8.608968  T2              0              1      T2
18  41.147532 -8.608707  T2              0              1      T2
19  41.148117 -8.608347  T2              0              1      T2
20  41.148351 -8.608149  T2              0              1      T2
21  41.148576 -8.608041  T2              0              1      T2
22  41.149260 -8.607654  T2            199              1      T2
23  41.149899 -8.607348  T2            199              1      T2
24  41.149899 -8.607393  T2            199              1      T2
25  41.149962 -8.607357  T2            199              1      T2
26  41.150979 -8.606817  T2            199              1      T2
27  41.151915 -8.606358  T2             90              1      T2
28  41.152788 -8.605719  T2             90              1      T2
29  41.153319 -8.604981  T2             90              1      T2
30  41.154345 -8.604783  T2            270              2      T2
31  41.154372 -8.604828  T2            270              2      T2
32  41.155353 -8.604801  T2            270              2      T2
33  41.156775 -8.604648  T2            270             -1      -1
34  41.158197 -8.604522  T2            184              3   T2334
35  41.159943 -8.604513  T2            184              3   T2334
36  41.160555 -8.604378  T2            184              3   T2334
37  41.160600 -8.604378  T2            184              3   T2334
38  41.160645 -8.604369  T2            184              3   T2334
39  41.160807 -8.604360  T2            184              3   T2334
40  41.161176 -8.604162  T2            184              3   T2334
41  41.161248 -8.604126  T2            184              3   T2334
42  41.161293 -8.604090  T2            184              3   T2334
43  41.161266 -8.604090  T2            184              3   T2334
44  41.161239 -8.604108  T2            184              3   T2334
45  41.161194 -8.604126  T2            184              3   T2334
46  41.161275 -8.604135  T2            184              3   T2334
47  41.162049 -8.603910  T2            184              3   T2334
48  41.162832 -8.602929  T2            184             -1      -1
49  41.163111 -8.602551  T2            184             -1      -1
50  41.163597 -8.601894  T2            123             -1      -1
51  41.148558 -8.585739  T3             23              0      T3
52  41.148828 -8.585730  T3             23              0      T3
53  41.148972 -8.585721  T3             23              0      T3
54  41.149017 -8.586288  T3             23              0      T3
55  41.148567 -8.586117  T3             23              0      T3
56  41.148315 -8.586198  T3             23              0      T3
57  41.147919 -8.586279  T3             23              0      T3
58  41.147325 -8.587152  T3             23              0      T3
59  41.146839 -8.585685  T3             23        

In [92]:
polylines_subtracks = polylines[polylines.DBSCAN_labels>-1]
fig = px.line_mapbox(polylines_subtracks, lat="lat", lon="lon", color="new_ids", zoom=3, height=700)

fig.update_layout(mapbox_style="stamen-terrain", mapbox_zoom=12, mapbox_center_lat = 41.14,
    margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

In [ ]:
def align_tracks(track1, track2, gap_penalty):
    """ Needleman-Wunsch algorithm adapted for gps tracks. """
    
    _log.info("Aligning tracks")

    def similarity(p1, p2):
        d = gpxpy.geo.distance(p1.latitude, p1.longitude, p1.elevation,
                               p2.latitude, p2.longitude, p2.elevation)
        return -d

    # construct f-matrix
    f = numpy.zeros((len(track1), len(track2)))
    for i in range(0, len(track1)):
        f[i][0] = gap_penalty * i
    for j in range(0, len(track2)):
        f[0][j] = gap_penalty * j
    for i in range(1, len(track1)):
        t1 = track1[i]
        for j in range(1, len(track2)):
            t2 = track2[j]
            match = f[i-1][j-1] + similarity(t1, t2)
            delete = f[i-1][j] + gap_penalty
            insert = f[i][j-1] + gap_penalty
            f[i, j] = max(match, max(delete, insert))

    # backtrack to create alignment
    a1 = []
    a2 = []
    i = len(track1) - 1
    j = len(track2) - 1
    while i > 0 or j > 0:
        if i > 0 and j > 0 and \
           f[i, j] == f[i-1][j-1] + similarity(track1[i], track2[j]):
            a1.insert(0, track1[i])
            a2.insert(0, track2[j])
            i -= 1
            j -= 1
        elif i > 0 and f[i][j] == f[i-1][j] + gap_penalty:
            a1.insert(0, track1[i])
            a2.insert(0, None)
            i -= 1
        elif j > 0 and f[i][j] == f[i][j-1] + gap_penalty:
            a1.insert(0, None)
            a2.insert(0, track2[j])
            j -= 1
    return a1, a2

align_tracks()